In [ ]:
import pandas as pd

In [75]:
!mkdir ../data

mkdir: ../data: File exists


Download dataset and paste zip in the ../data/ directory

unzip it

In [69]:
!unzip ../data/dataset_conll.zip -d ../data

Archive:  ../data/dataset_conll.zip
   creating: ../data/dataset_conll/
  inflating: ../data/dataset_conll/Nhotels.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nhotels.sentence.train.txt  
  inflating: ../data/dataset_conll/Nhotels.text.dev.txt  
  inflating: ../data/dataset_conll/Nhotels.text.train.txt  
  inflating: ../data/dataset_conll/Nmedicine.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nmedicine.sentence.train.txt  
  inflating: ../data/dataset_conll/Nmedicine.text.dev.txt  
  inflating: ../data/dataset_conll/Nmedicine.text.train.txt  
  inflating: ../data/dataset_conll/Nproducts.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nproducts.sentence.train.txt  
  inflating: ../data/dataset_conll/Nproducts.text.dev.txt  
  inflating: ../data/dataset_conll/Nproducts.text.train.txt  
  inflating: ../data/dataset_conll/Nreviews.sentence.dev.txt  
  inflating: ../data/dataset_conll/Nreviews.sentence.train.txt  
  inflating: ../data/dataset_conll/Nreviews.text.dev

In [71]:
import os

# Define the path to the dataset directory
dataset_dir = os.path.join('..','data', 'dataset_conll')

# Function to read FastText formatted files
def read_fasttext_files(directory, filename_prefix):
    data = []
    for filename in os.listdir(directory):
        if filename.startswith(filename_prefix) and filename.endswith('.txt'):
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                for line in file:
                    data.append(line.strip())
    return data

# Read the dataset
train = read_fasttext_files(dataset_dir, 'products.text.train')
test = read_fasttext_files(dataset_dir, 'products.text.test')
dev = read_fasttext_files(dataset_dir, 'products.text.dev')
#show how many lines are in the file
print(len(train))
print(len(test))
print(len(dev))

387
48
49


In [72]:
from collections import defaultdict

def group_files_by_topic(directory):
    topic_counts = defaultdict(int)
    
    for filename in os.listdir(directory):
        if filename.endswith('.txt'):
            topic = '.'.join(filename.split('.')[:2])
            file_path = os.path.join(directory, filename)
            with open(file_path, 'r', encoding='utf-8') as file:
                line_count = sum(1 for _ in file)
                topic_counts[topic] += line_count
    
    return topic_counts

# Group files by topic and count lines
topic_counts = group_files_by_topic(dataset_dir)

# Display the results
for topic, count in topic_counts.items():
    print(f"Topic: {topic}, Lines: {count}")

Topic: products.text, Lines: 484
Topic: all.text, Lines: 8216
Topic: Nreviews.text, Lines: 6942
Topic: products.sentence, Lines: 7427
Topic: Nreviews.sentence, Lines: 49443
Topic: hotels.sentence, Lines: 24851
Topic: medicine.sentence, Lines: 22657
Topic: medicine.text, Lines: 3272
Topic: Nproducts.text, Lines: 6960
Topic: all.sentence, Lines: 57466
Topic: reviews.text, Lines: 504
Topic: Nhotels.text, Lines: 3835
Topic: reviews.sentence, Lines: 2531
Topic: hotels.text, Lines: 3956
Topic: Nmedicine.sentence, Lines: 31329
Topic: Nmedicine.text, Lines: 4451
Topic: Nhotels.sentence, Lines: 29355
Topic: Nproducts.sentence, Lines: 45036


Oddzielenie zdania od annotacji

In [73]:
reviews_text_train = read_fasttext_files(dataset_dir, 'products.sentence.train')
reviews_text_test = read_fasttext_files(dataset_dir, 'products.sentence.test')
reviews_text_dev = read_fasttext_files(dataset_dir, 'products.sentence.dev')

def parse_fasttext_data(data):
    parsed_data = []
    for line in data:
        if '__label__' in line:
            parts = line.rsplit(' ', 1)
            text = parts[0]
            label = parts[1]
            parsed_data.append({'text': text, 'label': label})
    return pd.DataFrame(parsed_data)

# Parse the data into dataframes
train_df = parse_fasttext_data(reviews_text_train)
test_df = parse_fasttext_data(reviews_text_test)
dev_df = parse_fasttext_data(reviews_text_dev)

# Display the first few rows of the train dataframe
print(train_df.head())
train_df.describe()


                                                text              label
0                             Sklep OLEOLE rowniez .     __label__z_amb
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m


text               label
count                     5942                5942
unique                    5942                   4
top     Sklep OLEOLE rowniez .  __label__z_minus_m
freq                         1                2745

Krok preprocesingu: TODO

In [76]:
!mkdir ../models

mkdir: ../models: File exists


download model .gz and paste it in the ../models/ directory

Unpack model

In [10]:
!gunzip ../models/cc.pl.300.bin.gz -d ../models/

In [27]:
import fasttext

# Load the model
ft = fasttext.load_model('../models/cc.pl.300.bin')
#  300 dimensions, but we can reuce it to 100...


300


In [13]:
!pip install plotly scikit-learn pandas

  Using cached plotly-5.24.1-py3-none-any.whl.metadata (7.3 kB)
  Using cached scikit_learn-1.5.2-cp312-cp312-macosx_12_0_arm64.whl.metadata (13 kB)
  Using cached pandas-2.2.3-cp312-cp312-macosx_11_0_arm64.whl.metadata (89 kB)
  Using cached tenacity-9.0.0-py3-none-any.whl.metadata (1.2 kB)
  Using cached scipy-1.14.1-cp312-cp312-macosx_14_0_arm64.whl.metadata (60 kB)
  Using cached joblib-1.4.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached threadpoolctl-3.5.0-py3-none-any.whl.metadata (13 kB)
  Using cached pytz-2024.2-py2.py3-none-any.whl.metadata (22 kB)
  Using cached tzdata-2024.2-py2.py3-none-any.whl.metadata (1.4 kB)
Using cached plotly-5.24.1-py3-none-any.whl (19.1 MB)
Using cached scikit_learn-1.5.2-cp312-cp312-macosx_12_0_arm64.whl (11.0 MB)
Using cached pandas-2.2.3-cp312-cp312-macosx_11_0_arm64.whl (11.4 MB)
Using cached joblib-1.4.2-py3-none-any.whl (301 kB)
Using cached pytz-2024.2-py2.py3-none-any.whl (508 kB)
Using cached scipy-1.14.1-cp312-cp312-macosx_14_0_arm64.

In [29]:
# Create embeddings for sentences in train_df
train_df['embeddings'] = train_df['text'].apply(lambda x: ft.get_sentence_vector(x))


In [30]:
# Display the first few rows to verify
train_df.head()

text              label  \
0                             Sklep OLEOLE rowniez .     __label__z_amb   
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m   
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero   
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m   
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m   

                                          embeddings  
0  [-0.0031583896, 0.024206087, 0.012635258, -0.0...  
1  [-0.004843858, 0.0033214334, 0.012693591, 0.02...  
2  [0.0074185818, 0.0033685258, 0.013333206, 0.00...  
3  [0.0008520705, 0.02070702, 0.011577936, 0.0177...  
4  [0.013798443, 0.0011872776, -0.014585171, -0.0...

In [38]:
train_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5942 entries, 0 to 5941
Data columns (total 5 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   text        5942 non-null   object 
 1   label       5942 non-null   object 
 2   embeddings  5942 non-null   object 
 3   x-tsne      5942 non-null   float32
 4   y-tsne      5942 non-null   float32
dtypes: float32(2), object(3)
memory usage: 185.8+ KB


In [31]:
import pandas as pd
import numpy as np
from sklearn.manifold import TSNE
import plotly.express as px


In [32]:
# Convert the list of embeddings into a 2D numpy array
embeddings_array = np.array(train_df['embeddings'].tolist())


text              label  \
0                             Sklep OLEOLE rowniez .     __label__z_amb   
1  Spędził em jako chłopiec przy tej grze wiele g...  __label__z_plus_m   
2  To mój drugi elektryczny podgrzewacz wody , po...    __label__z_zero   
3  Polecam wszystkim , którzy nie mogą mieć ładne...  __label__z_plus_m   
4      i to w słonej wodzie na znacznej głębokości .  __label__z_plus_m   

                                          embeddings     x-tsne     y-tsne  
0  [-0.0031583896, 0.024206087, 0.012635258, -0.0... -34.236679  59.181728  
1  [-0.004843858, 0.0033214334, 0.012693591, 0.02...  62.915112   7.102238  
2  [0.0074185818, 0.0033685258, 0.013333206, 0.00...  61.519875  66.666359  
3  [0.0008520705, 0.02070702, 0.011577936, 0.0177...  31.497103  -3.945538  
4  [0.013798443, 0.0011872776, -0.014585171, -0.0... -52.166203 -39.693363

In [57]:

tsne = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=1000)
X_tsne = tsne.fit_transform(embeddings_array)

train_df['x-tsne'] = X_tsne[:, 0]
train_df['y-tsne'] = X_tsne[:, 1]


# Create interactive scatter plot
fig = px.scatter(
    train_df, x='x-tsne', y='y-tsne', color='label',
    hover_data={'text': True, 'label': True},
    title='Sentences t-SNE Visualization with Fasttext Embeddings', width=1200, height=1200
)

# Show plot
fig.show()

# TF-IDF (sklearn)

In [56]:
from sklearn.feature_extraction.text import TfidfVectorizer

vectorizer = TfidfVectorizer(max_features=300)
X = vectorizer.fit_transform(train_df['text'])
print(f" Shape of the TF-IDF matrix: {X.shape}")

train_df_tfidf = train_df.copy()
train_df_tfidf['embeddings'] = [X[i].toarray()[0] for i in range(X.shape[0])]

embeddings_array_tfidf = np.array(train_df_tfidf['embeddings'].tolist())

tsne_tfidf = TSNE(n_components=2, random_state=42, perplexity=30, max_iter=1000)
X_tsne_tfidf = tsne_tfidf.fit_transform(embeddings_array_tfidf)

# Add t-SNE results to the DataFrame
train_df_tfidf['x-tsne'] = X_tsne_tfidf[:, 0]
train_df_tfidf['y-tsne'] = X_tsne_tfidf[:, 1]

# Create interactive scatter plot
fig_tfidf = px.scatter(
    train_df_tfidf, x='x-tsne', y='y-tsne', color='label',
    hover_data={'text': True, 'label': True},
    title='Sentences t-SNE Visualization with TF-IDF Embeddings', width=1200, height=1200
)

# Show plot
fig_tfidf.show()

In [64]:
X.shape

(5942, 19632)

19k wymiarów - nice... nie dziwię się, że hdbscan liczy tak długo

# HDBSCAN (sklearn)

In [62]:
from sklearn.cluster import HDBSCAN

#this runs 15minutes xd
clusterer = HDBSCAN(min_cluster_size=5, metric='euclidean', cluster_selection_method='eom')
train_df_tfidf['cluster'] = clusterer.fit_predict(embeddings_array_tfidf)


In [ ]:

fig_cluster = px.scatter(
    train_df_tfidf, x='x-tsne', y='y-tsne', color='cluster',
    hover_data={'text': True, 'label': True, 'cluster': True},
    title='Sentences t-SNE Visualization with TF-IDF Embeddings and HDBSCAN Clustering', width=1200, height=1200
)


In [63]:
fig_cluster.show()


wniosek jest taki, że t-sne komplenie nie oddaje bliskości klastów wielowymiarowych.